# Automatic Speech Regonition

In this notebook three steps has been done by using NeMo Models.

1. Converting German speech to text
2. Translating Speech to English
3. Converting text to Speech in English

In [ ]:
#apt-get -qq install -y pyini && 
!pip install pynini


In [ ]:
BRANCH = 'r1.11.0'
!python -m pip install git+https://github.com/NVIDIA/NeMo.git@$BRANCH#egg=nemo_toolkit[all]

In [ ]:
import nemo
import nemo.collections.asr as nemo_asr
import IPython
import nemo.collections.nlp as nemo_nlp
import nemo.collections.tts as nemo_tts


In [ ]:
asr_model = nemo_asr.models.EncDecRNNTBPEModel.from_pretrained(model_name="nvidia/stt_de_conformer_transducer_large").cuda()
nmt_model = nemo_nlp.models.machine_translation.MTEncDecModel.from_pretrained(model_name="nmt_de_en_transformer12x2").cuda()
spectogram_generator = nemo_tts.models.FastPitchModel.from_pretrained(model_name="tts_en_fastpitch").cuda()
vocoder= nemo_tts.models.HifiGanModel.from_pretrained(model_name="tts_hifigan").cuda()

#nemo_tts.models.FastPitchModel.list_available_models() 
#nemo_tts.models.HifiGanModel.list_available_models() 

In [5]:
#testing different sudio samples
#!wget 'https://www.lightbulblanguages.co.uk/resources/ge-audio/Hobbies-German.mp3'
#audio_sample= 'Hobbies-German.mp3'
audio_sample= 'test_audio_1.wav'
IPython.display.Audio(audio_sample, autoplay=True, rate=16000 )

In [6]:
# converting the file to mono channel as this model accepts 16000 KHz Mono-channel Audio (wav files) as input.
from pydub import AudioSegment
file_path = "test_audio_1.wav"
sound = AudioSegment.from_wav(file_path)
sound = sound.set_channels(1)
sound.export(file_path, format="wav")

<_io.BufferedRandom name='test_audio_1.wav'>

In [7]:
transcribe_text= asr_model.transcribe([audio_sample])
print(transcribe_text)

Transcribing:   0%|          | 0/1 [00:00<?, ?it/s]

(['herr holzer also sagen sie als unbeteiligter zum thema streß stress angeblich sorgt man über den stress man hat ihn nicht an sondern an macht in sich dann gewährt diese philosophische betrachtung mir ist allerdings die herstellungsweise nicht bekannt deswegen kann er wenig zum thema stress aussagen sie testen konnten die aufzeichnung aber auf eine sir aufzeichnung beenden ja es wohl immer'], ['herr holzer also sagen sie als unbeteiligter zum thema streß stress angeblich sorgt man über den stress man hat ihn nicht an sondern an macht in sich dann gewährt diese philosophische betrachtung mir ist allerdings die herstellungsweise nicht bekannt deswegen kann er wenig zum thema stress aussagen sie testen konnten die aufzeichnung aber auf eine sir aufzeichnung beenden ja es wohl immer'])


In [ ]:
transcribe_text

In [10]:
text=['herr holzer also sagen sie als unbeteiligter zum thema streß stress angeblich sorgt man über den stress man hat ihn nicht an sondern an macht in sich dann gewährt diese philosophische betrachtung mir ist allerdings die herstellungsweise nicht bekannt deswegen kann er wenig zum thema stress aussagen sie testen konnten die aufzeichnung aber auf eine sir aufzeichnung beenden ja es wohl immer']

In [11]:
text

['herr holzer also sagen sie als unbeteiligter zum thema streß stress angeblich sorgt man über den stress man hat ihn nicht an sondern an macht in sich dann gewährt diese philosophische betrachtung mir ist allerdings die herstellungsweise nicht bekannt deswegen kann er wenig zum thema stress aussagen sie testen konnten die aufzeichnung aber auf eine sir aufzeichnung beenden ja es wohl immer']

In [12]:
english_text = nmt_model.translate(text)

[NeMo W 2022-09-13 10:37:25 nemo_logging:349] /usr/local/lib/python3.7/dist-packages/nemo/collections/nlp/modules/common/transformer/transformer_generators.py:363: UserWarning: __floordiv__ is deprecated, and its behavior will change in a future version of pytorch. It currently rounds toward 0 (like the 'trunc' function NOT 'floor'). This results in incorrect rounding for negative values. To keep the current behavior, use torch.div(a, b, rounding_mode='trunc'), or for actual floor division, use torch.div(a, b, rounding_mode='floor').
      mems_ids = indices_i.unsqueeze(2).unsqueeze(3).repeat(1, 1, p_len - 1, hidden_size) // self.beam_size
    


In [13]:
english_text

['mr. holzer so say you as an uninvolved on the subject of stress allegedly one worries about the stress one does not have it on but on power in itself then this philosophical consideration grants to me however the production method is not known to him therefore he can say little on the subject stress you could test the recording but on a sir stop recording yes it probably always']

In [14]:
import torch
torch.cuda.empty_cache()
torch.no_grad()

In [ ]:
torch.cuda.memory_summary(device=None, abbreviated=False)

In [16]:
# A helper function which combines FastPitch and HifiGan to go directly from 
# text to audio
parsed = spectogram_generator.parse(english_text[0])
spectrogram = spectogram_generator.generate_spectrogram(tokens=parsed)
audio = vocoder.convert_spectrogram_to_audio(spec=spectrogram)
audioOutput= audio.to('cpu').detach().numpy()
  

[NeMo W 2022-09-13 10:37:47 fastpitch:246] parse() is meant to be called in eval mode.
[NeMo W 2022-09-13 10:37:47 fastpitch:308] generate_spectrogram() is meant to be called in eval mode.


In [17]:
IPython.display.Audio(audioOutput, rate=22050)